In [1]:
import timesfm
from finetuning_torch import FinetuningConfig, TimesFMFinetuner
from torch.utils.data import Dataset

from timesfm import TimesFm, TimesFmCheckpoint, TimesFmHparams

import numpy as np
import pandas as pd

from functools import partial
import optuna

import gc

import os
import random
import time

import warnings
from warnings import simplefilter

from metrics_times import rrmse, pbe, pocid 
from sklearn.metrics import mean_absolute_percentage_error as mape

from os import path
from typing import Optional, Tuple
import torch
import torch.multiprocessing as mp
from huggingface_hub import snapshot_download


from timesfm.pytorch_patched_decoder import PatchedTimeSeriesDecoder

warnings.filterwarnings("ignore")
warnings.filterwarnings("ignore", category=UserWarning)
warnings.filterwarnings("ignore", category=RuntimeWarning)
warnings.filterwarnings("ignore", category=UserWarning, module="keras")
simplefilter(action='ignore', category=FutureWarning)

os.environ["CUDA_VISIBLE_DEVICES"] = "1"

 See https://github.com/google-research/timesfm/blob/master/README.md for updated APIs.


/home/user/miniconda3/envs/env_project_anp/lib/python3.11/site-packages/optuna/study/_optimize.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from optuna import progress_bar as pbar_module


Loaded PyTorch TimesFM, likely because python version is 3.11.9 | packaged by conda-forge | (main, Apr 19 2024, 18:36:13) [GCC 12.3.0].


In [2]:
class TimeSeriesDataset(Dataset):
  """Dataset for time series data compatible with TimesFM."""

  def __init__(self,
               series: np.ndarray,
               context_length: int,
               horizon_length: int,
               freq_type: int = 0):
    """
        Initialize dataset.

        Args:
            series: Time series data
            context_length: Number of past timesteps to use as input
            horizon_length: Number of future timesteps to predict
            freq_type: Frequency type (0, 1, or 2)
        """
    if freq_type not in [0, 1, 2]:
      raise ValueError("freq_type must be 0, 1, or 2")

    self.series = series
    self.context_length = context_length
    self.horizon_length = horizon_length
    self.freq_type = freq_type
    self._prepare_samples()

  def _prepare_samples(self) -> None:
    """Prepare sliding window samples from the time series."""
    self.samples = []
    total_length = self.context_length + self.horizon_length

    for start_idx in range(0, len(self.series) - total_length + 1):
      end_idx = start_idx + self.context_length
      x_context = self.series[start_idx:end_idx]
      x_future = self.series[end_idx:end_idx + self.horizon_length]
      self.samples.append((x_context, x_future))

  def __len__(self) -> int:
    return len(self.samples)

  def __getitem__(
      self, index: int
  ) -> Tuple[torch.Tensor, torch.Tensor, torch.Tensor, torch.Tensor]:
    x_context, x_future = self.samples[index]

    x_context = torch.tensor(x_context, dtype=torch.float32)
    x_future = torch.tensor(x_future, dtype=torch.float32)


    input_padding = torch.zeros_like(x_context)
    freq = torch.tensor([self.freq_type], dtype=torch.long)

    return x_context, input_padding, freq, x_future

def prepare_datasets(series: np.ndarray,
                     context_length: int,
                     horizon_length: int,
                     freq_type: int = 0) -> Tuple[Dataset, Dataset]:
  """
    Prepare training and validation datasets from time series data.

    Args:
        series: Input time series data
        context_length: Number of past timesteps to use
        horizon_length: Number of future timesteps to predict
        freq_type: Frequency type (0, 1, or 2)
        train_split: Fraction of data to use for training

    Returns:
        Tuple of (train_dataset, val_dataset)
    """
  
  train_size = int(len(series) * 0.5)
  train_data = series[:train_size]
  val_data = series[train_size:]

  # Create datasets with specified frequency type
  train_dataset = TimeSeriesDataset(train_data,
                                    context_length=context_length,
                                    horizon_length=horizon_length,
                                    freq_type=freq_type)

  val_dataset = TimeSeriesDataset(val_data,
                                  context_length=context_length,
                                  horizon_length=horizon_length,
                                  freq_type=freq_type)

  return train_dataset, val_dataset

In [3]:
def get_model(load_weights: bool = False, type_model: str = "500M"):
    device = "cuda" if torch.cuda.is_available() else "cpu"
    if type_model == "200M":
        repo_id = "google/timesfm-1.0-200m-pytorch"
        hparams = timesfm.TimesFmHparams(
            backend=device,
            per_core_batch_size=32,
            horizon_len=12,
        )
    else:
        repo_id = "google/timesfm-2.0-500m-pytorch"
        hparams = TimesFmHparams(
            backend=device,
            per_core_batch_size=32,
            horizon_len=12,
            num_layers=50,
            use_positional_embedding=False,
            context_len=32,
        )
    
    tfm = TimesFm(
        hparams=hparams,
        checkpoint=TimesFmCheckpoint(huggingface_repo_id=repo_id)
    )
    
    model = PatchedTimeSeriesDecoder(tfm._model_config)
    
    if load_weights:
        checkpoint_path = path.join(snapshot_download(repo_id), "torch_model.ckpt")
        loaded_checkpoint = torch.load(checkpoint_path, weights_only=True)
        model.load_state_dict(loaded_checkpoint)
    
    return model, hparams, tfm._model_config


In [ ]:
def plot_predictions(
    model: TimesFm,
    val_dataset: Dataset,
) -> None:
  """
    Plot model predictions against ground truth for a batch of validation data.

    Args:
      model: Trained TimesFM model
      val_dataset: Validation dataset
      save_path: Path to save the plot
    """

  model.eval()
  x_context, x_padding, freq, x_future = val_dataset[0]
  x_context = x_context.unsqueeze(0)  # Add batch dimension
  x_padding = x_padding.unsqueeze(0)
  freq = freq.unsqueeze(0)
  x_future = x_future.unsqueeze(0)

  device = next(model.parameters()).device
  x_context = x_context.to(device)
  x_padding = x_padding.to(device)
  freq = freq.to(device)
  x_future = x_future.to(device)

  with torch.no_grad():
    predictions = model(x_context, x_padding.float(), freq)
    predictions_mean = predictions[..., 0]  # [B, N, horizon_len]
    last_patch_pred = predictions_mean[:, -1, :]  # [B, horizon_len]

  context_vals = x_context[0].cpu().numpy()
  future_vals = x_future[0].cpu().numpy()
  pred_vals = last_patch_pred[0].cpu().numpy()

  context_len = len(context_vals)
  horizon_len = len(future_vals)

  return pred_vals[-12:]

In [5]:
# Function to convert a date string into a pandas Timestamp
def convert_date(date_string):
    """
    Convert a date string into a pandas Timestamp.

    Parameters:
    - date_string: str, date in 'YYYYMM' format

    Returns:
    - pd.Timestamp object representing the date
    """
    year_month = date_string.strip()
    year = int(year_month[:4])
    month = int(year_month[4:])
    return pd.Timestamp(year=year, month=month, day=1)

def objective(trial, df_train, y_test, df_mean, type_model, type_prediction, state, derivative):
    lr = trial.suggest_categorical("lr", [1e-3, 1e-4, 5e-5, 1e-6, 1e-7])
    epochs = trial.suggest_categorical("epochs", [5, 10, 20, 50, 80, 100])
    batch_size = trial.suggest_categorical("batch_size", [16, 32])

    print(f"\n=== Fine-tuning model {type_model} with parameters: ===")
    print(f"Fine-tuning:{type_prediction}")
    print(f"State:{state}")
    print(f"Derivative:{derivative}")
    print(f"Epoch:", epochs)
    print(f"Learning Rate:", lr)
    print(f"batch_size:", batch_size)

    model, hparams, tfm_config = get_model(type_model=type_model, load_weights=True)

    config = FinetuningConfig(batch_size=batch_size,
                            num_epochs=epochs,
                            learning_rate=lr,
                            use_wandb=False,
                            freq_type=1,
                            log_every_n_steps=10,
                            val_check_interval=0.5,
                            use_quantile_loss=True)
    
    if type_prediction == "fine_tuning_indiv":
        train_dataset, val_dataset = prepare_datasets(
            series= df_train['m3'].values,
            context_length=32,
            horizon_length=128,
            freq_type=1
        )

        print(f"Created datasets:")
        print(f"- Training samples: {len(train_dataset)}")
        print(f"- Validation samples: {len(val_dataset)}")
        print(f"- Using frequency type: {1}")
    
    finetuner = TimesFMFinetuner(model, config)

    print("\nStarting finetuning...")
    results = finetuner.finetune(train_dataset=train_dataset,
                                val_dataset=val_dataset)
    
    print("\nFinetuning completed!")
    print(f"Training history: {len(results['history']['train_loss'])} epochs")
    
    y_pred = plot_predictions(model=model, val_dataset=val_dataset)

    y_pred = [round(value, 3) for value in y_pred]

    rrmse_result = rrmse(y_test, y_pred, df_mean) 

    print(f"\nFine-tuning results of the TimesFM-{type_model} model \n")
    print(f'RRMSE: {rrmse_result}')
    return rrmse_result

def create_times_fm(
    state,
    derivative,
    df, 
    type_prediction='zeroshot',
    type_model='200M',
):
    """
    Runs a TimeFM model for time series forecasting.

    Parameters:
    - state (str): The specific state for which the model is trained.
    - derivative (str): The specific derivative for which the model is trained.
    - df (pd.DataFrame): The input DataFrame containing time series data.
    - type_prediction (str, optional): Specifies the prediction approach. Default is 'zeroshot'.
    - type_model (str, optional): Specifies the TimeFM model type. Choose from {'200M', '500M'}. Default is '200M'.

    Returns:
    - rrmse_result (float): Relative Root Mean Squared Error.
    - mape_result (float): Mean Absolute Percentage Error.
    - pbe_result (float): Percentage Bias Error.
    - pocid_result (float): Percentage of Correct Increase or Decrease.
    - mase_result (float): Mean Absolute Scaled Error.
    - y_pred (np.ndarray): Array containing the predicted values.
    - best_params (dict): The best hyperparameters found for the model.
    """

    df['timestamp'] = pd.to_datetime(df['timestamp'], errors='coerce')

    df['unique_id'] = 1
    df.rename(columns={'timestamp': 'ds'}, inplace=True)
    df = df[['unique_id', 'ds', 'm3']] 
    
    train_data = df.iloc[:-12]  
    test_data = df.iloc[-12:]  

    # INFO: ================== ZERO SHOT ==================
    if type_prediction == "zeroshot":
        best_params = None
        if type_model == '200M':
            model_tfm = timesfm.TimesFm(
                hparams=timesfm.TimesFmHparams(
                    backend="cuda",
                    per_core_batch_size=16,
                    horizon_len=12,
                ),
                checkpoint=timesfm.TimesFmCheckpoint(
                    huggingface_repo_id="google/timesfm-1.0-200m-pytorch"),
            )
        
        else:
            model_tfm = timesfm.TimesFm(
                hparams=timesfm.TimesFmHparams(
                    backend="cuda",
                    per_core_batch_size=16,                
                    horizon_len=12,
                    num_layers=50,
                    use_positional_embedding=False,
                    context_len=2048,
                ),
                checkpoint=timesfm.TimesFmCheckpoint(
                    huggingface_repo_id="google/timesfm-2.0-500m-pytorch"),
            )
        
        # forecast
        forecast_df = model_tfm.forecast_on_df(
                inputs=train_data,
                freq="M",  # monthly
                value_name="m3",
                num_jobs=-1,
            )

        y_pred = forecast_df["timesfm"].tolist()

    # INFO: ==================  FINE TUNING ==================
    elif type_prediction == "fine_tuning_indiv":

        study = optuna.create_study(direction="minimize", pruner=optuna.pruners.MedianPruner(n_warmup_steps=10))
        objective_func = partial(objective, 
                                df_train= train_data.iloc[:-12],
                                y_test= df["m3"][:-12][-12:].values,
                                df_mean= df["m3"][:-24].mean(),
                                type_model= type_model,
                                type_prediction= type_prediction,
                                state= state,
                                derivative= derivative)
    
        study.optimize(objective_func, n_trials=20)
        best_params = study.best_params
    
        print(f"\n=== Fine-tuning model {type_model} with parameters: ===")
        print(f"Fine-tuning: {type_prediction}")
        print(f"State: {state}")
        print(f"Derivative: {derivative}")
        print(f"Epoch: ", best_params["epochs"])
        print(f"Learning Rate: ", best_params["lr"])
        print(f"global_batch_size: ", best_params["batch_size"])

        # INFO: ==================  FINE TUNING MODEL ==================
        model, hparams, tfm_config = get_model(type_model=type_model, load_weights=True)

        config = FinetuningConfig(batch_size=best_params["batch_size"],
                                num_epochs=best_params["epochs"],
                                learning_rate=best_params["lr"],
                                use_wandb=False,
                                freq_type=1,
                                log_every_n_steps=10,
                                val_check_interval=0.5,
                                use_quantile_loss=True)
        
        if type_prediction == "fine_tuning_indiv":
            train_dataset, val_dataset = prepare_datasets(
                series= train_data['m3'].values,
                context_length=32,
                horizon_length=128,
                freq_type=1
            )

            print(f"Created datasets:")
            print(f"- Training samples: {len(train_dataset)}")
            print(f"- Validation samples: {len(val_dataset)}")
            print(f"- Using frequency type: {1}")
        
        finetuner = TimesFMFinetuner(model, config)

        print("\nStarting finetuning...")
        results = finetuner.finetune(train_dataset=train_dataset,
                                    val_dataset=val_dataset)
        
        print("\nFinetuning completed!")
        print(f"Training history: {len(results['history']['train_loss'])} epochs")
        
        y_pred = plot_predictions(model=model, val_dataset=val_dataset)

    y_pred = [round(value, 3) for value in y_pred]

    # Display results
    print("\nForecast for the last 12 months:")
    print(y_pred)

    print("\nActual values for the last 12 months:")
    print(test_data["m3"].tolist())

    y_test = df["m3"][-12:].values

    # Calculating evaluation metrics
    y_baseline = df["m3"][-12*2:-12].values
    rrmse_result = rrmse(y_test, y_pred, df["m3"][:-12].mean())
    mape_result = mape(y_test, y_pred)
    pbe_result = pbe(y_test, y_pred)
    pocid_result = pocid(y_test, y_pred)
    mase_result = np.mean(np.abs(y_test - y_pred)) / np.mean(np.abs(y_test - y_baseline))

    print(f"\nResultados TimesFM modelo: {type_model} \n")
    print(f'RRMSE: {rrmse_result}')
    print(f'MAPE: {mape_result}')
    print(f'PBE: {pbe_result}')
    print(f'POCID: {pocid_result}')
    print(f'MASE: {mase_result}')

    return rrmse_result, mape_result, pbe_result, pocid_result, mase_result, y_pred, best_params
            
def run_times_fm(state, derivative, data_filtered, type_prediction='zeroshot', type_model='200M'):

    # Record the start time of execution
    start_timestamp = time.strftime("%Y-%m-%d %H:%M:%S")
    print(f"\nExecution started at: {start_timestamp}")
    start_time = time.time()

    try:
        rrmse_result, mape_result, pbe_result, pocid_result, mase_result, y_pred, best_params = \
        create_times_fm(state=state,
                        derivative=derivative,
                        df=data_filtered, 
                        type_prediction=type_prediction, 
                        type_model=type_model)
        
        # Create a DataFrame to store the results
        results_df = pd.DataFrame([{'MODEL': 'TimesFM',
                                    'TYPE_MODEL': 'TimesFM_' + type_model,
                                    'TYPE_PREDICTIONS': type_prediction,
                                    'PARAMETERS': best_params,
                                    'STATE': state,
                                    'PRODUCT': derivative,
                                    'RRMSE': rrmse_result,
                                    'MAPE': mape_result,
                                    'PBE': pbe_result,
                                    'POCID': pocid_result,
                                    'MASE': mase_result,
                                    'PREDICTIONS': y_pred,
                                    'ERROR': np.nan}])
    except Exception as e:
        # Handle exceptions during model training
        print(f"An error occurred for product '{derivative}' in state '{state}': {e}")
        
        results_df = pd.DataFrame([{'MODEL': 'TimesFM',
                                    'TYPE_MODEL': 'TimesFM_' + type_model,
                                    'TYPE_PREDICTIONS': type_prediction,
                                    'PARAMETERS': np.nan,
                                    'STATE': state,
                                    'PRODUCT': derivative,
                                    'RRMSE': np.nan,
                                    'MAPE': np.nan,
                                    'PBE': np.nan,
                                    'POCID': np.nan,
                                    'MASE': np.nan,
                                    'PREDICTIONS': np.nan,
                                    'ERROR': f"An error occurred for product '{derivative}' in state '{state}': {e}"}])
            
    # Save the results to an Excel file if requested
    directory = f'results_model_local'
    if not os.path.exists(directory):
        os.makedirs(directory)

    file_path = os.path.join(directory, 'times_fm_results_last_year.xlsx')
    if os.path.exists(file_path):
        existing_df = pd.read_excel(file_path)
    else:
        existing_df = pd.DataFrame()

    combined_df = pd.concat([existing_df, results_df], ignore_index=True)
    combined_df.to_excel(file_path, index=False)

    ## Calculate and display the execution time
    end_time = time.time()
    execution_time = end_time - start_time
    print(f"Function execution time: {execution_time:.2f} seconds")
    print(f"Execution ended at: {time.strftime('%Y-%m-%d %H:%M:%S')}")

def run_all_in_thread(type_prediction='zeroshot', type_model='200M'):

    # Load the combined dataset
    all_data = pd.read_csv('../../database/combined_data.csv', sep=";")

    # Initialize a dictionary to store derivatives for each state
    state_derivative_dict = {}

    # Iterate over unique states
    for state in all_data['state'].unique():
        # Filter derivatives corresponding to this state
        derivatives = all_data[all_data['state'] == state]['product'].unique()
        # Add to the dictionary
        state_derivative_dict[state] = list(derivatives)

    # Loop through each state and its derivatives
    for state, derivatives in state_derivative_dict.items():
        for derivative in derivatives:
            print(f"========== State: {state}, derivative: {derivative} ==========")

            # Filter data for the current state and derivative
            data_filtered = all_data[(all_data['state'] == state) & (all_data['product'] == derivative)]
            
            run_times_fm(state, derivative, data_filtered, type_prediction, type_model)

def product_and_single_thread_testing():    
    state = "sp"
    derivative = "gasolinac"
    
    # Loading and preparing data
    data_filtered_test = pd.read_csv(f"../../database/venda_process/mensal/uf/{derivative}/mensal_{state}_{derivative}.csv", sep=";", parse_dates=['timestamp'], date_parser=convert_date)

    print(f" ========== Starting univariate test for the state of {state} - {derivative} ==========")

    # Recording start time of execution
    start_timestamp = time.strftime("%Y-%m-%d %H:%M:%S")
    print(f"\nExecution started at: {start_timestamp}")
    start_time = time.time()
    
    rrmse_result, mape_result, pbe_result, pocid_result, mase_result, y_pred, best_params = \
    create_times_fm(state=state,
                    derivative=derivative,
                    df=data_filtered_test,
                    type_prediction='fine_tuning_indiv', # zeroshot
                    type_model='200M') # 200M or 500M
    
    # Recording end time and calculating execution duration
    end_time = time.time()
    execution_time = end_time - start_time

    print(f"\nFunction execution time: {execution_time:.2f} seconds")
    print(f"Execution ended at: {time.strftime('%Y-%m-%d %H:%M:%S')}")

In [6]:
run_all_in_thread(type_prediction='fine_tuning_indiv', type_model='200M')

[I 2025-04-02 09:52:03,574] A new study created in memory with name: no-name-64ebd729-cee9-4ebd-8791-9b2d41d968c0


========== State: pe, derivative: etanolhidratado ==========

Execution started at: 2025-04-02 09:52:03

=== Fine-tuning model 200M with parameters: ===
Fine-tuning:fine_tuning_indiv
State:pe
Derivative:etanolhidratado
Epoch: 20
Learning Rate: 0.001
batch_size: 32


Fetching 3 files: 100%|██████████| 3/3 [00:00<00:00, 22550.02it/s]


Created datasets:
- Training samples: 34
- Validation samples: 34
- Using frequency type: 1

Starting finetuning...


[I 2025-04-02 09:52:08,615] Trial 0 finished with value: 2.0683558502827855 and parameters: {'lr': 0.001, 'epochs': 20, 'batch_size': 32}. Best is trial 0 with value: 2.0683558502827855.


...

Created datasets:
- Training samples: 34
- Validation samples: 34
- Using frequency type: 1

Starting finetuning...


[I 2025-04-02 21:39:45,497] Trial 19 finished with value: 0.07155737826541465 and parameters: {'lr': 5e-05, 'epochs': 100, 'batch_size': 16}. Best is trial 13 with value: 0.013975885819331102.



Finetuning completed!
Training history: 100 epochs

Fine-tuning results of the TimesFM-200M model 

RRMSE: 0.07155737826541465

=== Fine-tuning model 200M with parameters: ===
Fine-tuning: fine_tuning_indiv
State: ce
Derivative: queroseneiluminante
Epoch:  100
Learning Rate:  0.0001
global_batch_size:  16


Fetching 3 files: 100%|██████████| 3/3 [00:00<00:00, 81180.08it/s]


Created datasets:
- Training samples: 40
- Validation samples: 40
- Using frequency type: 1

Starting finetuning...

Finetuning completed!
Training history: 100 epochs

Forecast for the last 12 months:
[np.float32(9.409), np.float32(11.962), np.float32(7.246), np.float32(18.613), np.float32(8.829), np.float32(21.147), np.float32(7.55), np.float32(20.685), np.float32(8.936), np.float32(16.689), np.float32(7.4), np.float32(13.646)]

Actual values for the last 12 months:
[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]

Resultados TimesFM modelo: 200M 

RRMSE: 0.05764752342451743
MAPE: 5.708762869329647e+16
PBE: -inf
POCID: 0.0
MASE: inf
Function execution time: 226.83 seconds
Execution ended at: 2025-04-02 21:40:02
